# Jak stworzyć swojego robota?

## Narzędzia uruchamiane z wiersza poleceń

* wget
* curl
* aria2c

In [4]:
# Pobierz rekurencyjnie, z ograniczeniem do jednego poziomu rekurencji  
! wget -r -l 1 https://laboratoria.wmi.amu.edu.pl/

--2021-03-17 09:25:32--  https://laboratoria.wmi.amu.edu.pl/
Loaded CA certificate '/etc/ssl/certs/ca-certificates.crt'
Resolving laboratoria.wmi.amu.edu.pl (laboratoria.wmi.amu.edu.pl)... 150.254.78.3
Connecting to laboratoria.wmi.amu.edu.pl (laboratoria.wmi.amu.edu.pl)|150.254.78.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 6269 (6.1K) [text/html]
Saving to: 'laboratoria.wmi.amu.edu.pl/index.html'

laboratoria.wmi.amu 100%[===================>]   6.12K  --.-KB/s    in 0.001s  

2021-03-17 09:25:32 (4.19 MB/s) - 'laboratoria.wmi.amu.edu.pl/index.html' saved [6269/6269]

Loading robots.txt; please ignore errors.
--2021-03-17 09:25:32--  https://laboratoria.wmi.amu.edu.pl/robots.txt
Reusing existing connection to laboratoria.wmi.amu.edu.pl:443.
HTTP request sent, awaiting response... 403 Forbidden
2021-03-17 09:25:32 ERROR 403: Forbidden.

--2021-03-17 09:25:32--  https://laboratoria.wmi.amu.edu.pl/page-resources/wmi.png
Reusing existing connection to labo

In [7]:
# aria2c pozwala łatwo pobrać listę adresów URL, dla każdego adresu można ustawić specyficzne opcje
! (cd aria2c-example && cat aria.in)
! (cd aria2c-example && aria2c -i aria.in)

http://www.almanachmuszyny.pl/spisy/1991/AM1991_02_muszynski_zamek_prawda_i_legenda.pdf
     out=1991-1.pdf
http://www.almanachmuszyny.pl/spisy/1991/AM1991_03_muszyna_miasteczko_historyczne.pdf
     out=1991-2.pdf

03/17 09:31:54 [NOTICE] Downloading 2 item(s)

03/17 09:31:55 [NOTICE] Download complete: /home/filipg/ext/amu/aitech-eks/wyk/aria2c-example/1991-1.pdf

03/17 09:31:55 [NOTICE] Download complete: /home/filipg/ext/amu/aitech-eks/wyk/aria2c-example/1991-2.pdf

Download Results:
gid   |stat|avg speed  |path/URI
======+====+===========+=======================================================
3bf8a7|OK  |   458KiB/s|/home/filipg/ext/amu/aitech-eks/wyk/aria2c-example/1991-1.pdf
e0c4c1|OK  |   677KiB/s|/home/filipg/ext/amu/aitech-eks/wyk/aria2c-example/1991-2.pdf

Status Legend:
(OK):download completed.


## Biblioteki/frameworki do tworzenia robotów

### Python 

Użyteczne biblioteki: 

* urllib
* request
* Beautiful Soup (do parsowania HTML-a)

In [12]:
import urllib
import requests
from bs4 import BeautifulSoup

url = 'https://laboratoria.wmi.amu.edu.pl/'
response = requests.get(url)
soup = BeautifulSoup(response.content, "html.parser")

# wydobądź wszystkie linki (elementy A)
links = soup.find_all('a')
print([(link['href'], link.get_text()) for link in links])
    

[('/en/', 'English'), ('/', '\n\n      Laboratoria Komputerowe\n      '), ('/', 'Strona główna'), ('/godziny-otwarcia/', 'Godziny otwarcia'), ('/kontakt/', 'Kontakt'), ('/pierwsze-kroki/', 'Pierwsze kroki'), ('/przewodnik/', 'Przewodnik po stronie'), ('/regulamin-laboratoriow-komputerowych/', 'Regulamin Wydziałowych Laboratoriów Komputerowych'), ('/nie-odpowiadamy/', 'Za co nie odpowiadamy'), ('/laboratoria/oprogramowanie/', 'Laboratoria'), ('/uslugi/', 'Usługi'), ('/uslugi-uniwersyteckie/', 'Usługi Uniwersyteckie'), ('/problemy/docker/', 'Problemy'), ('/serwery-terminalowe/', 'serwera terminalowego'), ('/vpn/', 'VPN'), ('https://help.wmi.amu.edu.pl/', 'https://help.wmi.amu.edu.pl/'), ('/a126', 'A1-26'), ('https://help.wmi.amu.edu.pl/', 'System helpdeskowy'), ('mailto:helpdesk@wmi.amu.edu.pl', 'helpdesk@wmi.amu.edu.pl'), ('/irc', 'users'), ('https://www.facebook.com/wmilabs/', 'Facebook'), ('/godziny-otwarcia', 'Godziny otwarcia')]


## XPath

XPath – język służący do adresowania części dokumentu XML.

* `/html/body/div/p` – pełna ścieżka do wszystkich akapitów wewnątrz głównych elementów `<DIV>`
* `//div/p` – wszystkie akapity w jakichkolwiek elementach `<DIV>`
* `//a/@href` -  wartości atrybutu `href` dla wszystkich linków
* `//p[@id=’foo’]/img[5]` - piąty (indeksowanie od 1!) obrazek wewnątrz akapitu o  identyfikatorze foo
* `//p[img]/a` - linki w akapitach zawierających obrazek

Czym się różni:

* `//img[3]` od `(//img)[3]` ?
* `//p[img]/a` od `//p[//img]/a` ?




In [21]:

from urllib.request import urlopen
from lxml import etree

url = 'https://laboratoria.wmi.amu.edu.pl/'

response = urlopen(url)
htmlparser = etree.HTMLParser()
tree = etree.parse(response, htmlparser)
# linki z panelu
links = tree.xpath("//div[@class='sidebar-menu']//a/@href")
print(links)

['/', '/godziny-otwarcia/', '/kontakt/', '/pierwsze-kroki/', '/przewodnik/', '/regulamin-laboratoriow-komputerowych/', '/nie-odpowiadamy/', '/laboratoria/oprogramowanie/', '/uslugi/', '/uslugi-uniwersyteckie/', '/problemy/docker/']


## Jak poradzić sobie z dynamicznymi stronami?

### HtmlUnit

```
WebClient webClient = new WebClient();
HtmlPage page = webClient.getPage("http://ceti.pl/?ceti=administracja");

HtmlForm form = page.getForms().get(2);

HtmlTextInput loginField = form.getInputByName("login");
loginField.setValueAttribute("atrapa");
HtmlPasswordInput passField = form.getInputByName("pass");
passField.setValueAttribute("haslo1");

HtmlImageInput button = form.getInputByValue("OK");
HtmlPage page2 = (HtmlPage)button.click();

HtmlPage page3 = webClient.getPage("https://tau4.ceti.pl/cgi-bin/logs-user-show.cgi");
System.out.println(page3.asXml());

UnexpectedPage page4 = webClient.getPage("https://adm.tau4.ceti.pl/logs.zip");
InputStream istr = page4.getInputStream();
```                                         
                                         

## Selenium

In [2]:
# należy wcześniej uruchomić serwer selenium
# wget https://selenium-release.storage.googleapis.com/3.141/selenium-server-standalone-3.141.59.jar
# java -jar selenium-server-standalone-3.141.59.jar

from selenium import webdriver
from selenium.webdriver.common.desired_capabilities import DesiredCapabilities
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By

driver = webdriver.Remote(
   command_executor='http://127.0.0.1:4444/wd/hub',
   desired_capabilities=DesiredCapabilities.CHROME)

driver.get("http://www.python.org")
assert "Python" in driver.title
elem = driver.find_element_by_name("q")
elem.clear()
elem.send_keys("list")
elem.send_keys(Keys.RETURN)
links = driver.find_elements(By.XPATH, '//h3/a')
print([l.get_attribute('href') for l in links])
driver.close()

['https://www.python.org/community/sigs/guidelines', 'https://www.python.org/dev/peps/pep-0585/', 'https://www.python.org/community/lists', 'https://www.python.org/doc/essays/list2str', 'https://www.python.org/dev/core-mentorship', 'https://www.python.org/dev/peps/pep-3128/', 'https://www.python.org/dev/peps/pep-0204/', 'https://www.python.org/community/sigs/coordination', 'https://www.python.org/psf/committees', 'https://www.python.org/dev/peps/pep-0225/', 'https://www.python.org/dev/peps/pep-3132/', 'https://www.python.org/community/sigs/current/doc-sig/stext', 'https://www.python.org/dev/peps/pep-0202/', 'https://www.python.org/dev/peps/pep-0274/', 'https://www.python.org/dev/peps/pep-0469/', 'https://www.python.org/dev/peps/pep-0289/', 'https://www.python.org/dev/peps/pep-0270/', 'https://www.python.org/community/sigs/retired/string-sig', 'https://www.python.org/community/sigs/retired/progenv-sig', 'https://www.python.org/psf/records/board/minutes/2005-02-08']


## Haskell i strzałki

W języku Haskell można tworzyć roboty używając biblioteki HXT opartym na formalizmie strzałek (ang. _arrows_).
